In [ ]:
!unzip /content/ufo_enriched_v2.zip -d /content/

Archive:  /content/ufo_enriched_v2.zip
  inflating: /content/ufo_enriched_v2.jsonl  


In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Step 3 — BGE-Large embeddings for UFO corpus (A100-friendly)

Inputs
------
- /content/ufo_enriched_v2.jsonl
    * First line: metadata header (from merge pipeline)
    * Remaining lines: enriched UFO events with:
        - provenance fields (raw_snapshot, raw_hash, lineage, etc.)
        - macro context
        - moon metrics
        - geomagnetic latitude
        - nearest airport

Outputs
-------
- /content/ufo_bge_large_embeddings_v1.npz
    * ufo_uuid:      np.array of shape (N,), dtype=object (event IDs)
    * embeddings:    np.array of shape (N, 1024), dtype=float32

- /content/ufo_bge_large_embeddings_v1.meta.json
    * JSON with dataset + model + pipeline metadata

Notes
-----
- Only the WITNESS TEXT is embedded:
    * primary: full_text
    * fallback: summary
- Macro / moon / geomag / airports are NOT embedded here.
- Final “single file” with semantic dedupe will be built later
  by combining this NPZ with the enriched JSONL into
  ufo_semantic_v1.jsonl.
"""

import json
import os
from typing import List, Tuple

import numpy as np

from sentence_transformers import SentenceTransformer
import torch


# -------------------------------------------------------------------
# CONFIG
# -------------------------------------------------------------------
ENRICHED_PATH = "/content/ufo_enriched_v2.jsonl"
OUT_NPZ       = "/content/ufo_bge_large_embeddings_v1.npz"
OUT_META      = "/content/ufo_bge_large_embeddings_v1.meta.json"

EMBED_MODEL_NAME = "BAAI/bge-large-en-v1.5"
BATCH_SIZE       = 256   # Safe on A100, still OK on CPU if needed


# -------------------------------------------------------------------
# UTIL: Build text to embed for a row (witness text only)
# -------------------------------------------------------------------
def build_embed_text(row: dict) -> str:
    """
    Choose the field used for semantic embedding.

    Priority:
      1) full_text  (already your cleaned, merged narrative)
      2) summary
      3) fallback to "" (still encodable, but low information)
    """
    for key in ("full_text", "summary"):
        val = row.get(key)
        if isinstance(val, str) and val.strip():
            return val.strip()
    return ""


# -------------------------------------------------------------------
# LOAD DATA: split header vs. event rows
# -------------------------------------------------------------------
def load_enriched_events(path: str) -> Tuple[dict, List[str], List[str]]:
    """
    Reads ufo_enriched_v2.jsonl and returns:
      - header_obj: metadata header (first line with 'dataset' key)
      - uuids:      list of ufo_uuid strings
      - texts:      list of strings used for embedding (witness text)
    """
    header_obj = None
    uuids: List[str] = []
    texts: List[str] = []

    total_lines = 0
    events = 0

    print(f"Loading enriched JSONL from: {path}")
    with open(path, "r", encoding="utf-8") as f:
        for line in f:
            total_lines += 1
            line = line.strip()
            if not line:
                continue

            row = json.loads(line)

            # Treat the first line with 'dataset' as the header
            if header_obj is None and "dataset" in row and "merge_version" in row:
                header_obj = row
                continue

            # All event rows MUST have ufo_uuid (from your merge pipeline)
            ufo_id = row.get("ufo_uuid")
            if not isinstance(ufo_id, str):
                # If somehow no UUID, skip this row from embedding.
                continue

            text = build_embed_text(row)
            uuids.append(ufo_id)
            texts.append(text)
            events += 1

    print(f"Total lines read:  {total_lines}")
    print(f"Header present:    {'yes' if header_obj is not None else 'no'}")
    print(f"Events for embed:  {events}")
    return header_obj, uuids, texts


# -------------------------------------------------------------------
# MAIN
# -------------------------------------------------------------------
def main():
    # --------------------------
    # 1) Load data (header + events)
    # --------------------------
    header_obj, uuids, texts = load_enriched_events(ENRICHED_PATH)
    if not uuids:
        raise RuntimeError("No events with ufo_uuid found – check input file path / format.")

    # --------------------------
    # 2) Load BGE-Large model
    # --------------------------
    device = "cuda" if torch.cuda.is_available() else "cpu"
    print(f"\nLoading embedding model: {EMBED_MODEL_NAME} on device: {device}")
    model = SentenceTransformer(EMBED_MODEL_NAME, device=device)

    # --------------------------
    # 3) Encode all texts in batches
    # --------------------------
    print("\nEncoding texts with BGE-Large…")
    # SentenceTransformer handles batching internally
    embeddings = model.encode(
        texts,
        batch_size=BATCH_SIZE,
        show_progress_bar=True,
        normalize_embeddings=True,  # standard for BGE
    )

    embeddings = np.asarray(embeddings, dtype="float32")
    uuids_arr = np.asarray(uuids, dtype=object)

    print("\n=== EMBEDDING SUMMARY ===")
    print(f"Num events embedded: {len(uuids_arr):,}")
    print(f"Embedding shape:     {embeddings.shape}  (rows, dim)")
    print(f"Embedding dtype:     {embeddings.dtype}")

    # --------------------------
    # 4) Save NPZ (UUIDs + embeddings)
    # --------------------------
    np.savez(
        OUT_NPZ,
        ufo_uuid=uuids_arr,
        embeddings=embeddings,
    )
    print(f"\nSaved embeddings NPZ → {OUT_NPZ}")

    # --------------------------
    # 5) Save meta JSON
    # --------------------------
    meta = {
        "dataset": header_obj.get("dataset") if header_obj else "UFO Witness Corpus v2",
        "stage": "bge_large_embeddings_v1",
        "source_enriched_path": os.path.abspath(ENRICHED_PATH),
        "output_npz": os.path.abspath(OUT_NPZ),
        "embedding_model": EMBED_MODEL_NAME,
        "embedding_dim": int(embeddings.shape[1]),
        "normalize_embeddings": True,
        "batch_size": BATCH_SIZE,
        "num_events": int(embeddings.shape[0]),
    }

    with open(OUT_META, "w", encoding="utf-8") as f:
        json.dump(meta, f, ensure_ascii=False, indent=2)

    print(f"Saved meta JSON      → {OUT_META}")
    print("\nStep 3 complete. Use this NPZ in Step 4 (semantic clustering/dedupe).")


if __name__ == "__main__":
    main()


Loading enriched JSONL from: /content/ufo_enriched_v2.jsonl
Total lines read:  242843
Header present:    yes
Events for embed:  242842

Loading embedding model: BAAI/bge-large-en-v1.5 on device: cuda


/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

...

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/191 [00:00<?, ?B/s]


Encoding texts with BGE-Large…


Batches:   0%|          | 0/949 [00:00<?, ?it/s]


=== EMBEDDING SUMMARY ===
Num events embedded: 242,842
Embedding shape:     (242842, 1024)  (rows, dim)
Embedding dtype:     float32

Saved embeddings NPZ → /content/ufo_bge_large_embeddings_v1.npz
Saved meta JSON      → /content/ufo_bge_large_embeddings_v1.meta.json

Step 3 complete. Use this NPZ in Step 4 (semantic clustering/dedupe).


In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Step 3 — BGE-Large embedding sanity check

Validates:
  - NPZ file structure and shapes
  - Embedding norms (since we normalized)
  - Consistency between NPZ ufo_uuid list and enriched JSONL
  - Basic metadata consistency

Inputs
------
- /content/ufo_enriched_v2.jsonl
- /content/ufo_bge_large_embeddings_v1.npz
- /content/ufo_bge_large_embeddings_v1.meta.json  (optional but expected)

Run
---
python ufo_step3_validate_embeddings.py
"""

import os
import json
import numpy as np

ENRICHED_PATH = "/content/ufo_enriched_v2.jsonl"
NPZ_PATH      = "/content/ufo_bge_large_embeddings_v1.npz"
META_PATH     = "/content/ufo_bge_large_embeddings_v1.meta.json"


# ------------------------------------------------------------
# Helpers
# ------------------------------------------------------------
def load_enriched_uuids(path):
    """
    Stream the enriched JSONL and collect:
      - total event rows
      - set of ufo_uuid values
    Skips the header line that has 'dataset' / 'merge_version'.
    """
    total_lines = 0
    event_rows  = 0
    uuid_set    = set()

    header_seen = False

    print(f"Scanning enriched JSONL: {path}")
    with open(path, "r", encoding="utf-8") as f:
        for line in f:
            total_lines += 1
            line = line.strip()
            if not line:
                continue

            row = json.loads(line)

            # first header line
            if not header_seen and "dataset" in row and "merge_version" in row:
                header_seen = True
                continue

            event_rows += 1
            ufo_id = row.get("ufo_uuid")
            if isinstance(ufo_id, str):
                uuid_set.add(ufo_id)

    print(f"  Total lines (incl. header): {total_lines:,}")
    print(f"  Event rows (after header):  {event_rows:,}")
    print(f"  Unique event UUIDs:         {len(uuid_set):,}")
    return uuid_set, event_rows


def main():
    print("=== STEP 3 EMBEDDING VALIDATION ===\n")

    # -----------------------------
    # 1) Check files exist
    # -----------------------------
    for p in (ENRICHED_PATH, NPZ_PATH):
        if not os.path.exists(p):
            raise FileNotFoundError(f"Missing expected file: {p}")

    # META is optional but recommended
    meta = None
    if os.path.exists(META_PATH):
        with open(META_PATH, "r", encoding="utf-8") as f:
            meta = json.load(f)
        print("Loaded meta JSON:")
        print(json.dumps(meta, indent=2, ensure_ascii=False))
    else:
        print(f"WARNING: meta JSON not found at {META_PATH}")

    # -----------------------------
    # 2) Load NPZ
    # -----------------------------
    print("\nLoading NPZ embeddings:", NPZ_PATH)
    npz = np.load(NPZ_PATH, allow_pickle=True)

    if "ufo_uuid" not in npz or "embeddings" not in npz:
        raise KeyError("NPZ must contain 'ufo_uuid' and 'embeddings' arrays.")

    uuids_arr = npz["ufo_uuid"]
    emb = npz["embeddings"]

    print("\n=== NPZ STRUCTURE ===")
    print(f"ufo_uuid dtype: {uuids_arr.dtype}, shape: {uuids_arr.shape}")
    print(f"embeddings dtype: {emb.dtype}, shape: {emb.shape}")

    if emb.ndim != 2:
        raise ValueError(f"Expected embeddings to be 2D; got shape {emb.shape}")

    n_rows, dim = emb.shape

    if len(uuids_arr) != n_rows:
        raise ValueError(
            f"Mismatch: len(ufo_uuid)={len(uuids_arr)} vs embeddings rows={n_rows}"
        )

    # If meta is present, verify embedding_dim
    if meta is not None and "embedding_dim" in meta:
        expected_dim = int(meta["embedding_dim"])
        if dim != expected_dim:
            print(
                f"WARNING: embedding_dim in meta={expected_dim}, "
                f"but embeddings shape dim={dim}"
            )

    # -----------------------------
    # 3) Norm statistics
    # -----------------------------
    print("\n=== EMBEDDING NORM STATS ===")
    # norms over axis=1 (row direction)
    norms = np.linalg.norm(emb, axis=1)
    print(f"Min norm:   {norms.min():.6f}")
    print(f"Max norm:   {norms.max():.6f}")
    print(f"Mean norm:  {norms.mean():.6f}")
    print(f"Std norm:   {norms.std():.6f}")

    # If you normalized in encode(), these should all be ~1.0
    near_one_frac = float(np.mean((norms > 0.99) & (norms < 1.01)))
    print(f"Frac norms in [0.99, 1.01]: {near_one_frac*100:.2f}%")

    # -----------------------------
    # 4) UUID integrity checks
    # -----------------------------
    print("\n=== UUID INTEGRITY CHECK ===")
    uuid_set_npz = set(map(str, uuids_arr.tolist()))
    print(f"UUIDs in NPZ: {len(uuid_set_npz):,}")

    # Check if there are duplicates in NPZ
    if len(uuid_set_npz) != n_rows:
        print(
            f"WARNING: NPZ has duplicate UUIDs: "
            f"rows={n_rows:,}, unique_uuid={len(uuid_set_npz):,}"
        )
    else:
        print("No duplicate UUIDs in NPZ (good).")

    # -----------------------------
    # 5) Cross-check vs enriched JSONL
    # -----------------------------
    uuid_set_jsonl, event_rows = load_enriched_uuids(ENRICHED_PATH)

    missing_in_jsonl = uuid_set_npz - uuid_set_jsonl
    missing_in_npz   = uuid_set_jsonl - uuid_set_npz

    print("\n=== CROSS-CHECK (JSONL vs NPZ) ===")
    print(f"Events in JSONL (rows w/ UUID): {len(uuid_set_jsonl):,}")
    print(f"Events in NPZ (embedded UUIDs): {len(uuid_set_npz):,}")

    print(f"UUIDs in NPZ but NOT in JSONL:  {len(missing_in_jsonl):,}")
    print(f"UUIDs in JSONL but NOT in NPZ:  {len(missing_in_npz):,}")

    if missing_in_jsonl:
        print("  (This is unexpected – NPZ has UUIDs that JSONL doesn't.)")
    if missing_in_npz:
        print(
            "  (Expected if you deliberately skipped some rows; "
            "otherwise, check Step 3 input filtering.)"
        )

    print("\n=== DONE: STEP 3 VALIDATION ===")
    print("If norms ~1 and UUID counts align, embeddings look good.")
    print("You can now safely move on to Step 4 (semantic clustering/dedupe).")


if __name__ == "__main__":
    main()


=== STEP 3 EMBEDDING VALIDATION ===

Loaded meta JSON:
{
  "dataset": "UFO Witness Corpus v2",
  "stage": "bge_large_embeddings_v1",
  "source_enriched_path": "/content/ufo_enriched_v2.jsonl",
  "output_npz": "/content/ufo_bge_large_embeddings_v1.npz",
  "embedding_model": "BAAI/bge-large-en-v1.5",
  "embedding_dim": 1024,
  "normalize_embeddings": true,
  "batch_size": 256,
  "num_events": 242842
}

Loading NPZ embeddings: /content/ufo_bge_large_embeddings_v1.npz

=== NPZ STRUCTURE ===
ufo_uuid dtype: object, shape: (242842,)
embeddings dtype: float32, shape: (242842, 1024)

=== EMBEDDING NORM STATS ===
Min norm:   1.000000
Max norm:   1.000000
Mean norm:  1.000000
Std norm:   0.000000
Frac norms in [0.99, 1.01]: 100.00%

=== UUID INTEGRITY CHECK ===
UUIDs in NPZ: 242,839
Scanning enriched JSONL: /content/ufo_enriched_v2.jsonl
  Total lines (incl. header): 242,843
  Event rows (after header):  242,842
  Unique event UUIDs:         242,839

=== CROSS-CHECK (JSONL vs NPZ) ===
Events in 

In [ ]:
import zipfile
import os

meta_path = "/content/ufo_bge_large_embeddings_v1.meta.json"
npz_path  = "/content/ufo_bge_large_embeddings_v1.npz"
zip_path  = "/content/ufo_bge_large_embeddings_v1.zip"

if not os.path.exists(meta_path):
    raise FileNotFoundError(meta_path)
if not os.path.exists(npz_path):
    raise FileNotFoundError(npz_path)

with zipfile.ZipFile(zip_path, "w", compression=zipfile.ZIP_DEFLATED) as zf:
    zf.write(meta_path, arcname="ufo_bge_large_embeddings_v1.meta.json")
    zf.write(npz_path,  arcname="ufo_bge_large_embeddings_v1.npz")

print("Created ZIP:", zip_path)

# If you want to download in Colab:
# from google.colab import files
# files.download(zip_path)


Created ZIP: /content/ufo_bge_large_embeddings_v1.zip


In [ ]:
pip install hnswlib

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for hnswlib: filename=hnswlib-0.8.0-cp312-cp312-linux_x86_64.whl size=2528300 sha256=f350c9be93cd94cdc69127bfd281dccdfa37f3d1db6a9d830b7c3e940fe45532
  Stored in directory: /root/.cache/pip/wheels/ac/39/b3/cbd7f9cbb76501d2d5fbc84956e70d0b94e788aac87bda465e
Successfully built hnswlib


In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
STEP 4: Semantic clustering / dedupe over UFO Witness Corpus v2

Pipeline decisions:
- Operate at ROW level (each enriched row is a candidate event).
- Use BGE-large normalized embeddings (cosine via HNSW).
- Build clusters by thresholding cosine similarity and taking connected components.
- Preserve all original fields, including provenance.
- Output a new JSONL with one canonical row per semantic cluster.

Canonical selection rule (per cluster):
- Prefer rows with a geotemporal anchor (has_semantic_anchor = True:
  coordinates OR usable year_context_available).
- Then prefer rows with valid coordinates (has_coordinates = True).
- Then prefer earliest valid date (parsed_date_fill ASC).
- Then prefer longest narrative (full_text_len DESC).
- Then tie-break by ufo_uuid ASC, row_idx ASC.

NEW IN THIS VERSION:
- We DO NOT semantically cluster rows whose narrative text is non-informative
  (e.g. "nan", "none", "null", empty, etc.). Those remain singletons, which
  prevents one giant cluster of "nan" rows.
- We ONLY allow semantic clustering between rows whose full_text is long
  enough (>= MIN_TEXT_LEN_FOR_CLUSTERING characters). Short, generic one-line
  reports never chain into large clusters.
- Geotemporal anchors (coords/year) are used ONLY for picking the canonical
  representative inside each cluster; they do NOT gate clustering anymore.
"""

import json
import os
from collections import defaultdict

import numpy as np
import pandas as pd

try:
    import hnswlib
except ImportError:
    raise SystemExit(
        "hnswlib is required. Install it with:\n\n"
        "    pip install hnswlib\n"
    )

# ---------------------------------------------------------------------
# CONFIG
# ---------------------------------------------------------------------
META_PATH          = "/content/ufo_bge_large_embeddings_v1.meta.json"
DEFAULT_NPZ_PATH   = "/content/ufo_bge_large_embeddings_v1.npz"
DEFAULT_JSONL_PATH = "/content/ufo_enriched_v2.jsonl"
OUT_JSONL_PATH     = "/content/ufo_semantic_deduped_v1.jsonl"

# HNSW + clustering params (tunable but fixed here for reproducibility)
HNSW_SPACE         = "cosine"
HNSW_M             = 32
HNSW_EF_CONSTRUCT  = 200
HNSW_EF_SEARCH     = 100
HNSW_RANDOM_SEED   = 42

K_NEIGHBORS        = 10          # top-K neighbors per point
SIM_THRESHOLD      = 0.92        # cosine similarity threshold to consider "same event"

# Text length gate for clustering: only long, detailed narratives are eligible
MIN_TEXT_LEN_FOR_CLUSTERING = 120

# Text values that we treat as "non-informative" for semantic dedupe
# (these rows will not be merged via embeddings).
NULL_LIKE_TEXT = {"", "nan", "none", "null", "n/a", "na", "<na>"}


# ---------------------------------------------------------------------
# UNION-FIND (DISJOINT SET) FOR CLUSTERS
# ---------------------------------------------------------------------
class UnionFind:
    def __init__(self, n: int):
        self.parent = list(range(n))
        self.rank = [0] * n

    def find(self, x: int) -> int:
        # Path compression
        if self.parent[x] != x:
            self.parent[x] = self.find(self.parent[x])
        return self.parent[x]

    def union(self, a: int, b: int):
        ra = self.find(a)
        rb = self.find(b)
        if ra == rb:
            return
        # Union by rank
        if self.rank[ra] < self.rank[rb]:
            self.parent[ra] = rb
        elif self.rank[ra] > self.rank[rb]:
            self.parent[rb] = ra
        else:
            self.parent[rb] = ra
            self.rank[ra] += 1


# ---------------------------------------------------------------------
# SMALL HELPER: MAKE VALUES JSON-SERIALIZABLE
# ---------------------------------------------------------------------
def to_jsonable(v):
    """
    Normalize Pandas/NumPy scalars and timestamps into JSON-safe types.
    - np.generic / np.bool_ -> native Python scalar
    - pd.Timestamp -> ISO string or None if NaT
    - list/tuple -> recurse element-wise
    - dict -> recurse value-wise
    - NaN/NaT -> None
    """
    # NumPy scalar (int64, float64, bool_, etc.)
    if isinstance(v, (np.generic,)):
        return v.item()

    # Pandas timestamp
    if isinstance(v, pd.Timestamp):
        if pd.isna(v):
            return None
        return v.isoformat()

    # Lists / tuples: recurse
    if isinstance(v, (list, tuple)):
        return [to_jsonable(x) for x in v]

    # Dicts: recurse into values
    if isinstance(v, dict):
        return {str(k): to_jsonable(val) for k, val in v.items()}

    # Normalize NaN / NaT to None (scalar-like only)
    try:
        if pd.isna(v):
            return None
    except TypeError:
        # Non-numeric/non-datetime types -> ignore
        pass

    return v


# ---------------------------------------------------------------------
# LOAD META + EMBEDDINGS
# ---------------------------------------------------------------------
print("=== STEP 4: Semantic clustering / dedupe ===")

if not os.path.exists(META_PATH):
    raise FileNotFoundError(f"Meta JSON not found: {META_PATH}")

with open(META_PATH, "r", encoding="utf-8") as f:
    meta = json.load(f)

print("\nLoaded embedding meta JSON:")
print(json.dumps(meta, ensure_ascii=False, indent=2))

npz_path = meta.get("output_npz", DEFAULT_NPZ_PATH)
enriched_path = meta.get("source_enriched_path", DEFAULT_JSONL_PATH)

if not os.path.exists(npz_path):
    raise FileNotFoundError(f"Embeddings NPZ not found: {npz_path}")
if not os.path.exists(enriched_path):
    raise FileNotFoundError(f"Enriched JSONL not found: {enriched_path}")

print("\nLoading embeddings NPZ:", npz_path)
npz = np.load(npz_path, allow_pickle=True)

# Expect at least: embeddings, ufo_uuid
if "embeddings" not in npz or "ufo_uuid" not in npz:
    raise ValueError("NPZ must contain 'embeddings' and 'ufo_uuid' arrays.")

embeddings = npz["embeddings"]
ufo_uuid_arr = npz["ufo_uuid"]

n_vecs, dim = embeddings.shape
print(f"Embeddings shape: {embeddings.shape}")
print("First few UUIDs:", ufo_uuid_arr[:5])

# Sanity: norms ~1
norms = np.linalg.norm(embeddings, axis=1)
print("\nEmbedding norm stats:")
print("  min:", float(norms.min()))
print("  max:", float(norms.max()))
print("  mean:", float(norms.mean()))

# ---------------------------------------------------------------------
# LOAD ENRICHED JSONL (SKIP HEADER) & ALIGN
# ---------------------------------------------------------------------
print("\nLoading enriched JSONL rows from:", enriched_path)

rows = []
header_meta = None

with open(enriched_path, "r", encoding="utf-8") as f:
    # First line is dataset header
    first_line = f.readline()
    header_meta = json.loads(first_line)

    for idx, line in enumerate(f):
        line = line.strip()
        if not line:
            continue
        row = json.loads(line)
        row["__row_idx"] = idx  # 0..N-1
        rows.append(row)

print(f"Loaded rows (excluding header): {len(rows)}")

if len(rows) != n_vecs:
    raise ValueError(
        f"Mismatch: JSONL rows ({len(rows)}) vs embeddings ({n_vecs}). "
        "These must match 1:1 in order."
    )

# Build DataFrame for canonical selection later
df = pd.DataFrame(rows)
df["row_idx"] = df["__row_idx"].astype(int)
df.drop(columns=["__row_idx"], inplace=True)

# Sanity: ufo_uuid alignment
if "ufo_uuid" not in df.columns:
    raise ValueError("Expected 'ufo_uuid' column in enriched JSONL rows.")

jsonl_uuid = df["ufo_uuid"].astype(str).to_numpy()
npz_uuid   = ufo_uuid_arr.astype(str)

if len(jsonl_uuid) != len(npz_uuid):
    raise ValueError("UUID length mismatch between JSONL rows and NPZ.")

uuid_mismatch = np.sum(jsonl_uuid != npz_uuid)
print(f"UUID positional mismatches between JSONL and NPZ: {uuid_mismatch}")

if uuid_mismatch > 0:
    print("WARNING: There are positional UUID mismatches. "
          "We will still trust row-order alignment, but investigate if needed.")

# ---------------------------------------------------------------------
# DERIVE GEOTEMPORAL ANCHOR FLAG (for canonical selection ONLY)
# ---------------------------------------------------------------------
print("\nComputing geotemporal anchor mask (coords/year)...")

if "latitude" in df.columns and "longitude" in df.columns:
    coord_mask = df["latitude"].notna() & df["longitude"].notna()
else:
    coord_mask = pd.Series(False, index=df.index)

if "year_context_available" in df.columns:
    year_mask = df["year_context_available"].astype(bool)
elif "year" in df.columns:
    # Fallback: treat year >= 0 as usable
    year_mask = df["year"].astype(int) >= 0
else:
    year_mask = pd.Series(False, index=df.index)

df["has_semantic_anchor"] = coord_mask | year_mask
anchor_mask = df["has_semantic_anchor"].to_numpy()

# ---------------------------------------------------------------------
# TEXT INFORMATIVENESS + LENGTH MASKS
# ---------------------------------------------------------------------
print("\nComputing text informativeness mask for semantic clustering...")

df["full_text"] = df.get("full_text", df.get("summary", "")).astype(str)
full_text_norm = df["full_text"].str.strip().str.lower()
df["is_informative_text"] = ~full_text_norm.isin(NULL_LIKE_TEXT)
is_informative = df["is_informative_text"].to_numpy()

num_non_informative = int((~df["is_informative_text"]).sum())
num_informative = int(df["is_informative_text"].sum())

print(f"Non-informative text rows: {num_non_informative}")
print(f"Informative text rows:     {num_informative}")

# Length-based gate: only long, detailed narratives can form semantic edges
df["full_text_len"] = df["full_text"].str.len()
df["is_long_enough_for_cluster"] = df["full_text_len"] >= MIN_TEXT_LEN_FOR_CLUSTERING
long_enough_mask = df["is_long_enough_for_cluster"].to_numpy()

# ---------------------------------------------------------------------
# BUILD HNSW INDEX
# ---------------------------------------------------------------------
print("\nBuilding HNSW index...")
index = hnswlib.Index(space=HNSW_SPACE, dim=dim)
index.init_index(
    max_elements=n_vecs,
    ef_construction=HNSW_EF_CONSTRUCT,
    M=HNSW_M,
    random_seed=HNSW_RANDOM_SEED,
)

# embeddings are already normalized; for space='cosine' that is ideal
ids = np.arange(n_vecs, dtype=np.int32)
index.add_items(embeddings, ids)
index.set_ef(HNSW_EF_SEARCH)

print(f"HNSW index built with {n_vecs} elements, dim={dim}.")

# ---------------------------------------------------------------------
# KNN QUERY + CLUSTERING VIA UNION-FIND
# ---------------------------------------------------------------------
print("\nQuerying nearest neighbors and building clusters...")
uf = UnionFind(n_vecs)

BATCH = 10000
for start in range(0, n_vecs, BATCH):
    end = min(start + BATCH, n_vecs)
    batch_emb = embeddings[start:end]
    labels, distances = index.knn_query(batch_emb, k=K_NEIGHBORS)

    for i_rel in range(end - start):
        i = start + i_rel
        neigh_ids = labels[i_rel]
        neigh_dists = distances[i_rel]

        for j, dist in zip(neigh_ids, neigh_dists):
            if j == i:
                continue  # skip self

            # For space='cosine', distance = 1 - cos_sim
            cos_sim = 1.0 - float(dist)
            if cos_sim >= SIM_THRESHOLD:
                # Only cluster if BOTH i and j have:
                #  - informative text (not "nan"/"null"/etc.)
                #  - sufficiently long narrative (>= MIN_TEXT_LEN_FOR_CLUSTERING)
                if not (
                    is_informative[i]
                    and is_informative[j]
                    and long_enough_mask[i]
                    and long_enough_mask[j]
                ):
                    continue

                a, b = (i, j) if i < j else (j, i)
                uf.union(a, b)

print("Finished neighbor queries and unions.")

# ---------------------------------------------------------------------
# EXTRACT CLUSTERS
# ---------------------------------------------------------------------
print("\nExtracting connected components (semantic clusters)...")

root_to_indices = defaultdict(list)
for idx in range(n_vecs):
    root = uf.find(idx)
    root_to_indices[root].append(idx)

num_clusters = len(root_to_indices)
cluster_sizes = [len(v) for v in root_to_indices.values()]
num_collapsed = n_vecs - num_clusters

print(f"Total events (rows):     {n_vecs}")
print(f"Semantic clusters:       {num_clusters}")
print(f"Collapsed rows (N - C):  {num_collapsed}")
print("Cluster size stats:")
print("  min:", int(np.min(cluster_sizes)))
print("  max:", int(np.max(cluster_sizes)))
print("  mean:", float(np.mean(cluster_sizes)))

# ---------------------------------------------------------------------
# CHOOSE CANONICAL ROW PER CLUSTER (DETERMINISTIC)
# ---------------------------------------------------------------------
print("\nSelecting canonical row per cluster...")

# Parsed date (earlier is preferred). We treat unparseable as far-future.
df["parsed_date"] = pd.to_datetime(df.get("date_time", ""), errors="coerce")
df["parsed_date_fill"] = df["parsed_date"].fillna(pd.Timestamp.max)

# Geospatial integrity: has_coordinates (True if latitude & longitude present)
if "latitude" in df.columns and "longitude" in df.columns:
    df["has_coordinates"] = df["latitude"].notna() & df["longitude"].notna()
else:
    df["has_coordinates"] = False

# Attach cluster root + size
cluster_root = np.zeros(n_vecs, dtype=np.int64)
cluster_size_arr = np.zeros(n_vecs, dtype=np.int64)

for root, idxs in root_to_indices.items():
    size = len(idxs)
    for idx in idxs:
        cluster_root[idx] = root
        cluster_size_arr[idx] = size

df["semantic_cluster_root"] = cluster_root
df["semantic_cluster_size"] = cluster_size_arr

# Map each root to a consecutive cluster_id for nicer output
root_list = sorted(root_to_indices.keys())
root_to_cluster_id = {root: cid for cid, root in enumerate(root_list)}
df["semantic_cluster_id"] = df["semantic_cluster_root"].map(root_to_cluster_id).astype(int)

# Choose canonical per cluster with prioritized rules:
# has_semantic_anchor DESC,
# has_coordinates DESC,
# parsed_date_fill ASC,
# full_text_len DESC,
# ufo_uuid ASC,
# row_idx ASC
canonical_indices = []
canonical_cluster_id = []
for root, idxs in root_to_indices.items():
    sub = df.loc[idxs]
    sub_sorted = sub.sort_values(
        by=[
            "has_semantic_anchor",
            "has_coordinates",
            "parsed_date_fill",
            "full_text_len",
            "ufo_uuid",
            "row_idx",
        ],
        ascending=[False, False, True, False, True, True],
    )
    best_row_idx = int(sub_sorted.iloc[0]["row_idx"])
    canonical_indices.append(best_row_idx)
    canonical_cluster_id.append(root_to_cluster_id[root])

canonical_set = set(canonical_indices)
print(f"Canonical rows selected: {len(canonical_set)} (should equal num_clusters={num_clusters})")

# ---------------------------------------------------------------------
# WRITE OUTPUT JSONL (HEADER + CANONICAL ROWS ONLY)
# ---------------------------------------------------------------------
print(f"\nWriting semantic-deduped JSONL to: {OUT_JSONL_PATH}")

header_out = {
    "dataset": header_meta.get("dataset", "UFO Witness Corpus v2"),
    "stage": "semantic_dedup_hnsw_cosine_v1",
    "source_enriched_path": enriched_path,
    "source_embeddings_npz": npz_path,
    "embedding_model": meta.get("embedding_model", "BAAI/bge-large-en-v1.5"),
    "embedding_dim": int(meta.get("embedding_dim", embeddings.shape[1])),
    "normalize_embeddings": bool(meta.get("normalize_embeddings", True)),
    "hnswlib_params": {
        "space": HNSW_SPACE,
        "M": HNSW_M,
        "ef_construction": HNSW_EF_CONSTRUCT,
        "ef_search": HNSW_EF_SEARCH,
        "random_seed": HNSW_RANDOM_SEED,
    },
    "semantic_dedup_params": {
        "k_neighbors": K_NEIGHBORS,
        "sim_threshold": SIM_THRESHOLD,
        "min_text_len_for_clustering": MIN_TEXT_LEN_FOR_CLUSTERING,
        "canonical_priority": [
            "has_semantic_anchor DESC",
            "has_coordinates DESC",
            "parsed_date_fill ASC",
            "full_text_len DESC",
            "ufo_uuid ASC",
            "row_idx ASC",
        ],
        "text_informative_filter": {
            "null_like": sorted(list(NULL_LIKE_TEXT)),
        },
        "anchor_filter": "none (anchors affect canonical selection only, not clustering)",
    },
    "num_input_rows": int(n_vecs),
    "num_clusters": int(num_clusters),
    "num_collapsed_rows": int(num_collapsed),
    "num_informative_text_rows": int(num_informative),
    "num_non_informative_text_rows": int(num_non_informative),
}

with open(OUT_JSONL_PATH, "w", encoding="utf-8") as fout:
    # Header line
    fout.write(json.dumps(header_out, ensure_ascii=False) + "\n")

    for root, idxs in root_to_indices.items():
        cid = root_to_cluster_id[root]

        sub = df.loc[idxs]
        sub_sorted = sub.sort_values(
            by=[
                "has_semantic_anchor",
                "has_coordinates",
                "parsed_date_fill",
                "full_text_len",
                "ufo_uuid",
                "row_idx",
            ],
            ascending=[False, False, True, False, True, True],
        )
        best = sub_sorted.iloc[0]

        # build output record
        rec = {}

        # copy all original columns except helper/cluster internals
        for col in df.columns:
            if col in {
                "row_idx",
                "full_text_len",
                "parsed_date",
                "parsed_date_fill",
                "has_coordinates",
                "is_informative_text",
                "is_long_enough_for_cluster",
                "has_semantic_anchor",
                "semantic_cluster_root",
                "semantic_cluster_id",
                "semantic_cluster_size",
            }:
                continue
            rec[col] = best[col]

        # attach semantic cluster info
        rec["semantic_cluster_id"] = int(cid)
        rec["semantic_cluster_size"] = int(len(idxs))
        rec["semantic_cluster_members"] = [
            str(df.loc[i, "ufo_uuid"]) for i in idxs
        ]

        # normalize types for JSON
        clean_rec = {k: to_jsonable(v) for k, v in rec.items()}

        fout.write(json.dumps(clean_rec, ensure_ascii=False) + "\n")

print("=== DONE: Semantic dedupe written. ===")
print(f"Input rows: {n_vecs}")
print(f"Output rows (canonical): {num_clusters}")
print(f"Collapsed rows: {num_collapsed}")


=== STEP 4: Semantic clustering / dedupe ===

Loaded embedding meta JSON:
{
  "dataset": "UFO Witness Corpus v2",
  "stage": "bge_large_embeddings_v1",
  "source_enriched_path": "/content/ufo_enriched_v2.jsonl",
  "output_npz": "/content/ufo_bge_large_embeddings_v1.npz",
  "embedding_model": "BAAI/bge-large-en-v1.5",
  "embedding_dim": 1024,
  "normalize_embeddings": true,
  "batch_size": 256,
  "num_events": 242842
}

Loading embeddings NPZ: /content/ufo_bge_large_embeddings_v1.npz
Embeddings shape: (242842, 1024)
First few UUIDs: ['cc3690df331d32c1abd8954e41ce94de' '4f47228de56dbaa8215df1909f4292df'
 'a735c2455e6c6a14ba91362f2680edf4' '12961556ef8409be970e839f0b8bc5a8'
 '962866b542a3c0c34c98ca3d281307ac']

Embedding norm stats:
  min: 0.9999998807907104
  max: 1.0000001192092896
  mean: 1.0

Loading enriched JSONL rows from: /content/ufo_enriched_v2.jsonl
Loaded rows (excluding header): 242842
UUID positional mismatches between JSONL and NPZ: 0

Computing geotemporal anchor mask (coo

In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
STEP 4B: Semantic cluster sanity check

Purpose:
- Inspect the semantic cluster size distribution from STEP 4.
- Identify the largest cluster (e.g., 100k+ members) and analyze it:
  * shapes / countries distribution
  * coordinate coverage
  * text length stats
  * a few random example reports

Inputs:
  - /content/ufo_semantic_deduped_v1.jsonl
      (output of STEP 4 semantic dedupe; 1 line header + canonical rows)
  - /content/ufo_enriched_v2.jsonl
      (full enriched dataset with all original rows)

This script does NOT modify any files; it only prints diagnostics.
"""

import json
import os
from collections import Counter

import numpy as np
import pandas as pd
import random

SEM_DEDUP_PATH   = "/content/ufo_semantic_deduped_v1.jsonl"
ENRICHED_PATH    = "/content/ufo_enriched_v2.jsonl"

# Number of random samples to show from the mega cluster
N_SAMPLES = 10

print("=== STEP 4B: Semantic cluster sanity check ===\n")

if not os.path.exists(SEM_DEDUP_PATH):
    raise FileNotFoundError(f"Semantic-deduped JSONL not found: {SEM_DEDUP_PATH}")

if not os.path.exists(ENRICHED_PATH):
    raise FileNotFoundError(f"Enriched JSONL not found: {ENRICHED_PATH}")

# ---------------------------------------------------------------------
# 1) LOAD SEMANTIC-DEDUPED FILE & BUILD CLUSTER SIZE DISTRIBUTION
# ---------------------------------------------------------------------
print(f"Loading semantic-deduped file: {SEM_DEDUP_PATH}")

cluster_sizes = []
cluster_id_to_row = {}        # cluster_id -> canonical row (dict)
max_cluster_row = None
max_size = 0

with open(SEM_DEDUP_PATH, "r", encoding="utf-8") as f:
    header_line = f.readline().strip()
    header = json.loads(header_line)
    print("Header (summary):")
    print(json.dumps(header, indent=2, ensure_ascii=False))
    print()

    for line in f:
        line = line.strip()
        if not line:
            continue
        row = json.loads(line)

        cid = int(row.get("semantic_cluster_id", -1))
        csize = int(row.get("semantic_cluster_size", 1))

        cluster_sizes.append(csize)
        cluster_id_to_row[cid] = row

        if csize > max_size:
            max_size = csize
            max_cluster_row = row

num_clusters = len(cluster_sizes)
print(f"Canonical rows (clusters): {num_clusters}")
print(f"Min cluster size:          {int(np.min(cluster_sizes))}")
print(f"Max cluster size:          {int(np.max(cluster_sizes))}")
print(f"Mean cluster size:         {float(np.mean(cluster_sizes)):.3f}")
for q in [50, 75, 90, 95, 99]:
    print(f"{q}th percentile size:      {int(np.quantile(cluster_sizes, q/100.0))}")
print()

if max_cluster_row is None:
    raise RuntimeError("No clusters found in semantic-deduped file.")

mega_cid = int(max_cluster_row["semantic_cluster_id"])
mega_size = int(max_cluster_row["semantic_cluster_size"])
mega_members = max_cluster_row.get("semantic_cluster_members", [])

print("=== LARGEST CLUSTER ===")
print(f"Cluster ID:               {mega_cid}")
print(f"Cluster size:             {mega_size}")
print(f"Members listed:           {len(mega_members)}")
print()

# ---------------------------------------------------------------------
# 2) LOAD ENRICHED JSONL AND BUILD ufo_uuid -> ROW MAP
# ---------------------------------------------------------------------
print(f"Loading enriched JSONL for cluster inspection: {ENRICHED_PATH}")

uuid_to_row = {}

with open(ENRICHED_PATH, "r", encoding="utf-8") as f:
    # first line is header
    enriched_header_line = f.readline().strip()
    _ = json.loads(enriched_header_line)  # we don't actually need the contents here

    for line in f:
        line = line.strip()
        if not line:
            continue
        row = json.loads(line)
        uid = str(row.get("ufo_uuid"))
        if uid:
            uuid_to_row[uid] = row

print(f"Total enriched rows with UUID: {len(uuid_to_row):,}")
print()

# ---------------------------------------------------------------------
# 3) EXTRACT MEGA CLUSTER MEMBERS FROM ENRICHED DATA
# ---------------------------------------------------------------------
print("Extracting mega cluster members from enriched data...")

mega_rows = []
missing_count = 0

for uid in mega_members:
    uids = str(uid)
    r = uuid_to_row.get(uids)
    if r is not None:
        mega_rows.append(r)
    else:
        missing_count += 1

print(f"Mega cluster rows found:   {len(mega_rows)}")
print(f"Mega cluster rows missing: {missing_count}")
print()

if not mega_rows:
    raise RuntimeError("No rows for mega cluster were found in the enriched data.")

mega_df = pd.DataFrame(mega_rows)

# ---------------------------------------------------------------------
# 4) STATS ABOUT THE MEGA CLUSTER
# ---------------------------------------------------------------------
print("=== Mega cluster stats ===")

# Shapes
shape_counts = Counter(mega_df.get("shape", pd.Series(dtype=str)).astype(str))
print("\nTop shapes in mega cluster:")
for shape, cnt in shape_counts.most_common(10):
    print(f"  {shape!r:20s} -> {cnt}")

# Countries
country_counts = Counter(mega_df.get("country", pd.Series(dtype=str)).astype(str))
print("\nTop countries in mega cluster:")
for country, cnt in country_counts.most_common(10):
    print(f"  {country!r:20s} -> {cnt}")

# Coordinate coverage
has_lat = mega_df.get("latitude").notna() if "latitude" in mega_df.columns else pd.Series(False, index=mega_df.index)
has_lon = mega_df.get("longitude").notna() if "longitude" in mega_df.columns else pd.Series(False, index=mega_df.index)
has_coords = has_lat & has_lon
num_coords = int(has_coords.sum())
print(f"\nRows with valid coordinates: {num_coords} / {len(mega_df)} "
      f"({100.0 * num_coords / len(mega_df):.2f}%)")

# Text length stats
text_series = mega_df.get("full_text", mega_df.get("summary", pd.Series("", index=mega_df.index))).astype(str)
lengths = text_series.str.len().to_numpy()

print("\nText length stats (characters):")
print(f"  min:   {int(lengths.min())}")
print(f"  max:   {int(lengths.max())}")
print(f"  mean:  {float(lengths.mean()):.1f}")
for q in [50, 75, 90, 95, 99]:
    print(f"  {q}th percentile: {int(np.quantile(lengths, q/100.0))}")

# Date distribution (if parseable)
parsed_dates = pd.to_datetime(mega_df.get("date_time", ""), errors="coerce")
valid_dates = parsed_dates.dropna()
if not valid_dates.empty:
    print("\nDate range in mega cluster:")
    print(f"  earliest: {valid_dates.min()}")
    print(f"  latest:   {valid_dates.max()}")
else:
    print("\nNo parseable dates in mega cluster.")

# ---------------------------------------------------------------------
# 5) RANDOM SAMPLE OF EXAMPLE REPORTS
# ---------------------------------------------------------------------
print("\n=== Random sample of example reports from mega cluster ===")

if len(mega_rows) <= N_SAMPLES:
    sample_rows = mega_rows
else:
    sample_rows = random.sample(mega_rows, N_SAMPLES)

for i, r in enumerate(sample_rows, 1):
    city    = r.get("city")
    state   = r.get("state")
    country = r.get("country")
    dt      = r.get("date_time")
    shape   = r.get("shape")
    lat     = r.get("latitude")
    lon     = r.get("longitude")
    txt     = r.get("full_text") or r.get("summary") or ""
    txt_snip = txt[:260].replace("\n", " ")

    print("-" * 70)
    print(f"Sample #{i}")
    print(f"  ufo_uuid: {r.get('ufo_uuid')}")
    print(f"  date_time: {dt}")
    print(f"  location:  {city}, {state}, {country}")
    print(f"  coords:    {lat}, {lon}")
    print(f"  shape:     {shape}")
    print(f"  text[0:260]: {txt_snip!r}")

print("\n=== DONE: Mega cluster sanity check complete. ===")


=== STEP 4B: Semantic cluster sanity check ===

Loading semantic-deduped file: /content/ufo_semantic_deduped_v1.jsonl
Header (summary):
{
  "dataset": "UFO Witness Corpus v2",
  "stage": "semantic_dedup_hnsw_cosine_v1",
  "source_enriched_path": "/content/ufo_enriched_v2.jsonl",
  "source_embeddings_npz": "/content/ufo_bge_large_embeddings_v1.npz",
  "embedding_model": "BAAI/bge-large-en-v1.5",
  "embedding_dim": 1024,
  "normalize_embeddings": true,
  "hnswlib_params": {
    "space": "cosine",
    "M": 32,
    "ef_construction": 200,
    "ef_search": 100,
    "random_seed": 42
  },
  "semantic_dedup_params": {
    "k_neighbors": 10,
    "sim_threshold": 0.92,
    "min_text_len_for_clustering": 120,
    "canonical_priority": [
      "has_semantic_anchor DESC",
      "has_coordinates DESC",
      "parsed_date_fill ASC",
      "full_text_len DESC",
      "ufo_uuid ASC",
      "row_idx ASC"
    ],
    "text_informative_filter": {
      "null_like": [
        "",
        "<na>",
        "n

In [ ]:
!gzip -9 /content/ufo_semantic_deduped_v1.jsonl


In [ ]:
!zip -j /content/ufo_v2_clustered_bm25_v1.zip /content/ufo_v2_clustered_bm25_v1.jsonl

  adding: ufo_v2_clustered_bm25_v1.jsonl (deflated 89%)


In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
STEP 5: Topic clustering (HDBSCAN + PCA) + BM25-style cluster keywords
over the semantic-deduped UFO Witness Corpus v2.

Inputs:
  - /content/ufo_semantic_deduped_v1.jsonl   (canonical, semantically deduped)
  - /content/ufo_bge_large_embeddings_v1.npz (BGE-large embeddings for ALL events)

Outputs:
  - /content/ufo_v2_clustered_bm25_v1.jsonl  (single merged artifact)

Pipeline:
  1. Load semantic-deduped canonical rows.
  2. Map canonical ufo_uuid -> original BGE embeddings (1024D).
  3. PCA(1024 -> 64) for stability + speed.
  4. HDBSCAN on 64D for unsupervised topic clusters.
     - Only cluster rows with sufficiently long, informative text.
     - Others get cluster_id = -1 (noise/unclustered).
  5. BM25-style cluster keywords:
     - Tokenize all texts.
     - Compute df / idf across corpus.
     - For each cluster, compute tf_cluster * idf to get top tokens.
  6. Write one JSONL with:
     - Original canonical fields (including semantic_cluster_* from Step 4).
     - hdbscan_cluster_id, hdbscan_cluster_size
     - hdbscan_cluster_top_terms (list of strings)
     - All configs in header for full reproducibility.
"""

import json
import os
import re
from collections import Counter, defaultdict

import numpy as np
import pandas as pd

try:
    import hdbscan
except ImportError:
    raise SystemExit(
        "hdbscan is required. Install it with:\n\n"
        "    pip install hdbscan\n"
    )

from sklearn.decomposition import PCA

# ---------------------------------------------------------------------
# CONFIG
# ---------------------------------------------------------------------
SEMANTIC_DEDUP_JSONL = "/content/ufo_semantic_deduped_v1.jsonl"
EMBEDDINGS_NPZ_PATH  = "/content/ufo_bge_large_embeddings_v1.npz"
OUT_JSONL_PATH       = "/content/ufo_v2_clustered_bm25_v1.jsonl"

# PCA config
PCA_DIM         = 64
PCA_RANDOM_SEED = 42

# HDBSCAN config
# Tuned for more granular topics:
# - min_cluster_size = 15 (smaller, more clusters)
# - cluster_selection_method='leaf' to keep leaf clusters.
HDBSCAN_MIN_CLUSTER_SIZE = 15
HDBSCAN_MIN_SAMPLES      = 5
HDBSCAN_METRIC           = "euclidean"
HDBSCAN_CLUSTER_SELECTION_METHOD = "leaf"
HDBSCAN_ALPHA            = 1.0  # explicit, used in leaf selection

# Text filters for clustering
NULL_LIKE_TEXT = {"", "nan", "none", "null", "n/a", "na", "<na>"}
MIN_TEXT_LEN_FOR_CLUSTERING = 120  # only cluster reasonably long narratives

# BM25-style keyword scoring
BM25_TOP_TERMS_PER_CLUSTER = 15
BM25_MIN_DF = 5  # ignore tokens that appear in fewer than this many docs

# INTENTIONALLY MINIMAL STOPWORD LIST.
# We only strip pure grammatical glue. Domain words like "light", "object",
# "sky", "triangle", "bright", etc. are *the signal* in UFO narratives and
# must NOT be removed.
STOPWORDS = {
    "the", "and", "a", "an", "of", "to", "in", "for", "on", "at", "with",
    "it", "is", "was", "were", "be", "been", "are",
    "this", "that", "these", "those",
    "from", "by", "or", "as", "but",
    "have", "has", "had", "not", "no",
    "i", "we", "you", "they", "he", "she", "them", "his", "her",
}


# ---------------------------------------------------------------------
# HELPER: JSON-SERIALIZABLE
# ---------------------------------------------------------------------
def to_jsonable(v):
    """
    Normalize Pandas/NumPy scalars and timestamps into JSON-safe types.
    - np.generic / np.bool_ -> native Python scalar
    - pd.Timestamp -> ISO string or None if NaT
    - list/tuple -> recurse element-wise
    - dict -> recurse value-wise
    - NaN/NaT -> None
    """
    if isinstance(v, (np.generic,)):
        return v.item()

    if isinstance(v, pd.Timestamp):
        if pd.isna(v):
            return None
        return v.isoformat()

    if isinstance(v, (list, tuple)):
        return [to_jsonable(x) for x in v]

    if isinstance(v, dict):
        # avoid NameError by using local names
        return {str(kk): to_jsonable(vv) for kk, vv in v.items()}

    try:
        if pd.isna(v):
            return None
    except TypeError:
        pass

    return v


# ---------------------------------------------------------------------
# HELPER: TOKENIZE
# ---------------------------------------------------------------------
WORD_RE = re.compile(r"[a-z0-9]+")

def tokenize(text: str):
    text = text.lower()
    return WORD_RE.findall(text)


# ---------------------------------------------------------------------
# LOAD SEMANTIC-DEDUPED CANONICAL FILE
# ---------------------------------------------------------------------
print("=== STEP 5: HDBSCAN + BM25 cluster labeling ===")

if not os.path.exists(SEMANTIC_DEDUP_JSONL):
    raise FileNotFoundError(f"Semantic-deduped JSONL not found: {SEMANTIC_DEDUP_JSONL}")

print("\nLoading semantic-deduped canonical JSONL:", SEMANTIC_DEDUP_JSONL)

rows = []
header_meta = None
with open(SEMANTIC_DEDUP_JSONL, "r", encoding="utf-8") as f:
    first_line = f.readline()
    header_meta = json.loads(first_line)

    for line in f:
        line = line.strip()
        if not line:
            continue
        rows.append(json.loads(line))

df = pd.DataFrame(rows)
n_docs = len(df)
print(f"Canonical rows loaded: {n_docs}")

if "ufo_uuid" not in df.columns:
    raise ValueError("Expected 'ufo_uuid' column in semantic-deduped file.")

# Choose text column
TEXT_COL_CANDIDATES = ["full_text", "text", "summary"]
text_col = None
for c in TEXT_COL_CANDIDATES:
    if c in df.columns:
        text_col = c
        break

if text_col is None:
    raise ValueError(
        "No text column found. Expected one of: "
        f"{TEXT_COL_CANDIDATES}, but got columns: {list(df.columns)}"
    )

df[text_col] = df[text_col].fillna("").astype(str)
texts = df[text_col].to_numpy()

# ---------------------------------------------------------------------
# LOAD EMBEDDINGS NPZ AND MAP CANONICAL ROWS
# ---------------------------------------------------------------------
if not os.path.exists(EMBEDDINGS_NPZ_PATH):
    raise FileNotFoundError(f"Embeddings NPZ not found: {EMBEDDINGS_NPZ_PATH}")

print("\nLoading embeddings NPZ:", EMBEDDINGS_NPZ_PATH)
npz = np.load(EMBEDDINGS_NPZ_PATH, allow_pickle=True)

if "embeddings" not in npz or "ufo_uuid" not in npz:
    raise ValueError("NPZ must contain 'embeddings' and 'ufo_uuid' arrays.")

emb_all = npz["embeddings"]
uuids_all = npz["ufo_uuid"].astype(str)
n_all, emb_dim = emb_all.shape

print(f"Embeddings shape (full): {emb_all.shape}")

uuid_to_idx = {u: i for i, u in enumerate(uuids_all)}

canonical_uuids = df["ufo_uuid"].astype(str).to_numpy()
canon_indices = np.empty(n_docs, dtype=np.int64)

missing = 0
for i, u in enumerate(canonical_uuids):
    idx = uuid_to_idx.get(u, -1)
    if idx < 0:
        missing += 1
        canon_indices[i] = -1
    else:
        canon_indices[i] = idx

if missing > 0:
    raise ValueError(
        f"{missing} canonical rows have ufo_uuid not found in embeddings NPZ."
    )

emb_canon = emb_all[canon_indices]
print(f"Canonical embeddings shape: {emb_canon.shape}")

# ---------------------------------------------------------------------
# BUILD TEXT FILTER MASK FOR CLUSTERING
# ---------------------------------------------------------------------
print("\nComputing clustering text mask...")

full_text_norm = pd.Series(texts).str.strip().str.lower()
is_non_informative = full_text_norm.isin(NULL_LIKE_TEXT)
is_informative = ~is_non_informative

text_len = full_text_norm.str.len()
long_enough = text_len >= MIN_TEXT_LEN_FOR_CLUSTERING

cluster_mask = (is_informative & long_enough).to_numpy()
n_clusterable = int(cluster_mask.sum())

print(f"Clusterable docs (informative & len >= {MIN_TEXT_LEN_FOR_CLUSTERING}): {n_clusterable}")
print(f"Non-clusterable docs: {n_docs - n_clusterable}")

# ---------------------------------------------------------------------
# PCA REDUCTION
# ---------------------------------------------------------------------
print("\nRunning PCA reduction (1024 ->", PCA_DIM, ")...")

pca = PCA(
    n_components=PCA_DIM,
    random_state=PCA_RANDOM_SEED,
)
X_pca = pca.fit_transform(emb_canon)
print("PCA embedding shape:", X_pca.shape)

# ---------------------------------------------------------------------
# HDBSCAN CLUSTERING
# ---------------------------------------------------------------------
print("\nRunning HDBSCAN on clusterable subset...")

X_cluster = X_pca[cluster_mask]

if n_clusterable == 0:
    print("WARNING: No docs passed clustering mask; all will be noise.")
    labels_sub = np.full((0,), -1, dtype=int)
else:
    clusterer = hdbscan.HDBSCAN(
        min_cluster_size=HDBSCAN_MIN_CLUSTER_SIZE,
        min_samples=HDBSCAN_MIN_SAMPLES,
        metric=HDBSCAN_METRIC,
        cluster_selection_method=HDBSCAN_CLUSTER_SELECTION_METHOD,
        alpha=HDBSCAN_ALPHA,
        core_dist_n_jobs=-1,  # use all cores
    )
    labels_sub = clusterer.fit_predict(X_cluster)

# Map back to full doc index
hdbscan_labels = np.full(n_docs, -1, dtype=int)
clusterable_indices = np.where(cluster_mask)[0]
for i, doc_idx in enumerate(clusterable_indices):
    hdbscan_labels[doc_idx] = int(labels_sub[i])

# Compute cluster sizes
cluster_size_counter = Counter(int(l) for l in hdbscan_labels if l >= 0)
hdbscan_cluster_size = np.array(
    [cluster_size_counter.get(int(l), 0) if l >= 0 else 0 for l in hdbscan_labels],
    dtype=int,
)

num_clusters = len(cluster_size_counter)
num_noise = int((hdbscan_labels < 0).sum())

print("\nHDBSCAN clustering stats:")
print(f"  HDBSCAN clusters (label >=0): {num_clusters}")
print(f"  Noise / unclustered (label = -1): {num_noise}")

if num_clusters > 0:
    print("  Max cluster size:", max(cluster_size_counter.values()))
    print("  Min cluster size:", min(cluster_size_counter.values()))
else:
    print("  No non-noise clusters found.")

# ---------------------------------------------------------------------
# BM25-STYLE CLUSTER KEYWORDS
# ---------------------------------------------------------------------
print("\nComputing BM25-style cluster keywords...")

# Tokenize all texts
tokens_all = []
df_counter = Counter()  # document frequency
for i, txt in enumerate(texts):
    toks = tokenize(txt)
    toks = [t for t in toks if t not in STOPWORDS]
    tokens_all.append(toks)

    seen = set()
    for t in toks:
        if t not in seen:
            df_counter[t] += 1
            seen.add(t)

N = n_docs
idf = {}
for t, df_t in df_counter.items():
    if df_t < BM25_MIN_DF:
        continue
    # BM25-ish idf (no length norm, just weighting)
    idf_val = np.log(1.0 + (N - df_t + 0.5) / (df_t + 0.5))
    idf[t] = float(idf_val)

print(f"Vocabulary size after df >= {BM25_MIN_DF}: {len(idf)}")

# Build mapping from cluster_id -> doc indices
cluster_to_docs = defaultdict(list)
for idx, cid in enumerate(hdbscan_labels):
    if cid >= 0:
        cluster_to_docs[cid].append(idx)

cluster_top_terms = {}  # cid -> list[str]
for cid, doc_ids in cluster_to_docs.items():
    tf_cluster = Counter()
    for idx in doc_ids:
        for t in tokens_all[idx]:
            if t in idf:  # skip tokens filtered out of idf
                tf_cluster[t] += 1

    if not tf_cluster:
        cluster_top_terms[cid] = []
        continue

    # score = tf_cluster * idf
    scores = []
    for t, tf_val in tf_cluster.items():
        scores.append((t, tf_val * idf.get(t, 0.0)))

    scores.sort(key=lambda x: x[1], reverse=True)
    top_terms = [t for (t, _) in scores[:BM25_TOP_TERMS_PER_CLUSTER]]
    cluster_top_terms[cid] = top_terms

print("Finished computing cluster keywords.")

# ---------------------------------------------------------------------
# WRITE MERGED OUTPUT JSONL
# ---------------------------------------------------------------------
print(f"\nWriting merged clustered+BM25 JSONL to: {OUT_JSONL_PATH}")

header_out = {
    "dataset": header_meta.get("dataset", "UFO Witness Corpus v2"),
    "stage": "semantic_dedup_hdbscan_bm25_v1",
    "source_semantic_dedup_jsonl": SEMANTIC_DEDUP_JSONL,
    "source_embeddings_npz": EMBEDDINGS_NPZ_PATH,
    "embedding_model": header_meta.get("embedding_model", "BAAI/bge-large-en-v1.5"),
    "embedding_dim": int(header_meta.get("embedding_dim", emb_dim)),
    "semantic_dedup_params": header_meta.get("semantic_dedup_params", {}),
    "pca_params": {
        "n_components": PCA_DIM,
        "random_state": PCA_RANDOM_SEED,
        "fit_on": "canonical_embeddings",
    },
    "hdbscan_params": {
        "min_cluster_size": HDBSCAN_MIN_CLUSTER_SIZE,
        "min_samples": HDBSCAN_MIN_SAMPLES,
        "metric": HDBSCAN_METRIC,
        "cluster_selection_method": HDBSCAN_CLUSTER_SELECTION_METHOD,
        "alpha": HDBSCAN_ALPHA,
        "core_dist_n_jobs": -1,
    },
    "clustering_text_filter": {
        "min_text_len_for_clustering": MIN_TEXT_LEN_FOR_CLUSTERING,
        "null_like": sorted(list(NULL_LIKE_TEXT)),
    },
    "bm25_params": {
        "top_terms_per_cluster": BM25_TOP_TERMS_PER_CLUSTER,
        "min_df": BM25_MIN_DF,
        "stopwords_size": len(STOPWORDS),
        "tokenizer": "regex [a-z0-9]+, lowercased",
    },
    "num_docs_canonical": int(n_docs),
    "num_docs_clusterable": int(n_clusterable),
    "num_hdbscan_clusters": int(num_clusters),
    "num_hdbscan_noise_docs": int(num_noise),
}

with open(OUT_JSONL_PATH, "w", encoding="utf-8") as fout:
    fout.write(json.dumps(header_out, ensure_ascii=False) + "\n")

    for i in range(n_docs):
        row = df.iloc[i].to_dict()

        # Attach HDBSCAN info
        cid = int(hdbscan_labels[i])
        row["hdbscan_cluster_id"] = cid
        row["hdbscan_cluster_size"] = int(hdbscan_cluster_size[i])

        if cid >= 0:
            row["hdbscan_cluster_top_terms"] = cluster_top_terms.get(cid, [])
        else:
            row["hdbscan_cluster_top_terms"] = []

        clean_rec = {k: to_jsonable(v) for k, v in row.items()}
        fout.write(json.dumps(clean_rec, ensure_ascii=False) + "\n")

print("=== DONE: HDBSCAN + BM25 clustering written. ===")
print(f"Output rows: {n_docs}")
print(f"HDBSCAN clusters: {num_clusters}, noise docs: {num_noise}")


=== STEP 5: HDBSCAN + BM25 cluster labeling ===

Loading semantic-deduped canonical JSONL: /content/ufo_semantic_deduped_v1.jsonl
Canonical rows loaded: 242633

Loading embeddings NPZ: /content/ufo_bge_large_embeddings_v1.npz
Embeddings shape (full): (242842, 1024)
Canonical embeddings shape: (242633, 1024)

Computing clustering text mask...
Clusterable docs (informative & len >= 120): 35027
Non-clusterable docs: 207606

Running PCA reduction (1024 -> 64 )...
PCA embedding shape: (242633, 64)

Running HDBSCAN on clusterable subset...


/usr/local/lib/python3.12/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(



HDBSCAN clustering stats:
  HDBSCAN clusters (label >=0): 7
  Noise / unclustered (label = -1): 242246
  Max cluster size: 111
  Min cluster size: 19

Computing BM25-style cluster keywords...
Vocabulary size after df >= 5: 9082
Finished computing cluster keywords.

Writing merged clustered+BM25 JSONL to: /content/ufo_v2_clustered_bm25_v1.jsonl
=== DONE: HDBSCAN + BM25 clustering written. ===
Output rows: 242633
HDBSCAN clusters: 7, noise docs: 242246


In [18]:
import json, pandas as pd

MASTER_PATH = "/content/ufo_v2_clustered_bm25_v1.jsonl"

with open(MASTER_PATH, "r", encoding="utf-8") as f:
    header = json.loads(f.readline())
header


{'dataset': 'UFO Witness Corpus v2',
 'stage': 'semantic_dedup_hdbscan_bm25_v1',
 'source_semantic_dedup_jsonl': '/content/ufo_semantic_deduped_v1.jsonl',
 'source_embeddings_npz': '/content/ufo_bge_large_embeddings_v1.npz',
 'embedding_model': 'BAAI/bge-large-en-v1.5',
 'embedding_dim': 1024,
 'semantic_dedup_params': {'k_neighbors': 10,
  'sim_threshold': 0.92,
  'min_text_len_for_clustering': 120,
  'canonical_priority': ['has_semantic_anchor DESC',
   'has_coordinates DESC',
   'parsed_date_fill ASC',
   'full_text_len DESC',
   'ufo_uuid ASC',
   'row_idx ASC'],
  'text_informative_filter': {'null_like': ['',
    '<na>',
    'n/a',
    'na',
    'nan',
    'none',
    'null']},
  'anchor_filter': 'none (anchors affect canonical selection only, not clustering)'},
 'pca_params': {'n_components': 64,
  'random_state': 42,
  'fit_on': 'canonical_embeddings'},
 'hdbscan_params': {'min_cluster_size': 15,
  'min_samples': 5,
  'metric': 'euclidean',
  'cluster_selection_method': 'leaf',


In [17]:
required_cols = [
    "ufo_uuid",
    "full_text",      # or your main narrative column
    "semantic_cluster_id",
    "semantic_cluster_size",
    "semantic_cluster_members",
    "hdbscan_cluster_id",
    "hdbscan_cluster_size",
    "hdbscan_cluster_top_terms",
]

missing = [c for c in required_cols if c not in df.columns]
missing


['hdbscan_cluster_id', 'hdbscan_cluster_size', 'hdbscan_cluster_top_terms']

In [4]:
import json
import pandas as pd

PATH = "/content/ufo_v2_clustered_bm25_v1.jsonl"

rows = []
with open(PATH, "r", encoding="utf-8") as f:
    header = json.loads(f.readline())  # keep if you want metadata
    for line in f:
        line = line.strip()
        if not line:
            continue
        rows.append(json.loads(line))

df = pd.DataFrame(rows)
print("Rows loaded:", len(df))
print(df.columns.tolist())


Rows loaded: 242633
['city', 'state', 'date_time', 'shape', 'duration_bucket', 'text_hash', 'raw_snapshot', 'raw_hash', 'summary', 'full_text', 'duration_seconds', 'latitude', 'longitude', 'country', 'year', 'year_context_available', 'ufo_uuid', 'lineage', 'merge_version', 'dedupe_method', 'nchs_nchs_top_five_leading_causes_of_death_united_states_1990_1950_2000_number_of_deaths', 'nchs_nchs_age_adjusted_death_rates_for_selected_major_causes_of_death_age_adjusted_death_rate', 'nchs_nchs_death_rates_and_life_expectancy_at_birth_average_life_expectancy_years', 'nchs_nchs_death_rates_and_life_expectancy_at_birth_age_adjusted_death_rate', 'nchs_nchs_leading_causes_of_death_united_states_deaths', 'nchs_nchs_leading_causes_of_death_united_states_age_adjusted_death_rate', 'nchs_nchs_potentially_excess_deaths_from_the_five_leading_causes_of_death_hhs_region', 'nchs_nchs_potentially_excess_deaths_from_the_five_leading_causes_of_death_observed_deaths', 'nchs_nchs_potentially_excess_deaths_from_th

In [5]:
# 1) How many docs per cluster (including noise)
df["hdbscan_cluster_id"].value_counts().sort_index()


hdbscan_cluster_id
-1    242246
 0        25
 1        19
 2        52
 3       111
 4        85
 5        26
 6        69
Name: count, dtype: int64

In [6]:
# 2) Fraction that actually landed in a cluster
total = len(df)
noise = (df["hdbscan_cluster_id"] < 0).sum()
clustered = total - noise
total, clustered, noise, clustered / total


(242633, np.int64(387), np.int64(242246), np.float64(0.0015950015043295841))

In [7]:
# 3) Inspect clusters + top terms + sample rows
text_col = "full_text"  # or "summary" if that's what you used

for cid in sorted(df["hdbscan_cluster_id"].unique()):
    if cid < 0:
        continue
    sub = df[df["hdbscan_cluster_id"] == cid]
    print("="*80)
    print(f"Cluster {cid} | size={len(sub)}")
    print("Top terms:", sub["hdbscan_cluster_top_terms"].iloc[0])
    print("Sample rows:")
    for _, row in sub.sample(min(5, len(sub)), random_state=0)[
        ["date_time", "city", "state", "shape", text_col]
    ].iterrows():
        print("---", row["date_time"], "|", row["city"], row["state"], "|", row["shape"])
        print(row[text_col][:300].replace("\n", " "))
        print()


Cluster 0 | size=25
Top terms: ['2003', 'occurred', 'reported', 'entered', '10', '00', 'posted', 'am', 'report', 'ago', 'location', '2004', '23', 'happened', '2005']
Sample rows:
--- nan | Gulfport MS | triangle
NOTE:  I received a letter from the witness on 07/16/00.  I sent her a letter asking if she would like to file an offfical report with 

--- nan | Cape Coral FL | triangle
I never reported this, but since I found this website, thought I would in case anyone else may have reported something around the same

--- nan | Seattle WA | circle
This event occurred many years ago when I was eight. I have never spoken publicly of it, but now, at the age of 45, I am interested in 

--- nan | Phoenix AZ | nan
Occurred : 5/19/2005 10:35 (Entered as : 05/19/1905 10:35) Reported: 5/20/2005 1:37:11 AM 01:37 Posted: 5/24/2005 Location: Phoenix (90

--- nan | Montague NJ | circle
WELL,FIRST ID REALLY LIKE WHOMEVER IS GOING TO READ THIS TO KNOW THAT I AM REALLY HAVING A HARD TIME   BELIEVING THIS 